In [16]:
import librosa
import numpy as np
from python_speech_features import mfcc, fbank, logfbank, ssc, base
import matplotlib.pyplot as plt


import os
from scipy.fftpack import dct
from tqdm import tqdm
import pickle

In [17]:
def extract_plp_from_mp3(file_path, sr=16000, n_ceps=13, winlen=0.025, winstep=0.01, 
                         nfilt=26, nfft=512, lowfreq=0, highfreq=None, preemph=0.97):
    """
    Extract PLP coefficients from an MP3 file.
    
    Parameters:
    -----------
    file_path : str
        Path to the MP3 file
    sr : int
        Sample rate to load the audio with
    n_ceps : int
        Number of cepstral coefficients
    winlen : float
        Window length in seconds
    winstep : float
        Window step in seconds
    nfilt : int
        Number of filters in the filterbank
    nfft : int
        FFT size
    lowfreq : int
        Lowest band edge of mel filters
    highfreq : int
        Highest band edge of mel filters
    preemph : float
        Pre-emphasis coefficient
    
    Returns:
    --------
    plp_features : ndarray
        PLP coefficients
    """
    # Load audio file
    y, sr = librosa.load(file_path, sr=sr, mono=True)
    
    # Get PLP coefficients using python_speech_features
    # First we need to get filterbank energies
    fbank_feat = base.fbank(y, samplerate=sr, winlen=winlen, winstep=winstep,
                          nfilt=nfilt, nfft=nfft, lowfreq=lowfreq, highfreq=highfreq,
                          preemph=preemph)
    
    # Then apply PLP-like processing
    # Note: python_speech_features doesn't have direct PLP implementation,
    # so we'll use a simplified approach that mimics PLP processing
    
    # 1. Get filter bank energies
    fb_energies = fbank_feat[0]
    
    # 2. Apply equal-loudness curve and cubic-root compression (simplified PLP)
    # This is a simplified version - true PLP involves more steps
    loudness_fb = np.power(fb_energies, 0.33)  # Cube root compression
    
    # 3. Apply DCT (similar to MFCC computation)
    from scipy.fftpack import dct
    plp_coeffs = dct(loudness_fb, type=2, axis=1, norm='ortho')[:, :n_ceps]
    
    return plp_coeffs

def plot_plp_coefficients(plp_coeffs, output_path, sr=16000, winstep=0.01):
    """
    Plot PLP coefficients as a heatmap and save to file.
    """
    plt.figure(figsize=(10, 6))
    plt.imshow(plp_coeffs.T, aspect='auto', origin='lower')
    plt.title('PLP Coefficients')
    plt.ylabel('PLP Coefficient Index')
    plt.xlabel('Frame')
    
    # Set x-axis labels to reflect time in seconds
    plt.colorbar(label='Coefficient Value')
    
    # Set x-tick labels to show time in seconds
    x_ticks = np.arange(0, plp_coeffs.shape[0], max(1, int(plp_coeffs.shape[0]/5)))
    x_tick_labels = [f"{t * winstep:.1f}" for t in x_ticks]
    plt.xticks(x_ticks, x_tick_labels)
    
    plt.tight_layout()
    plt.savefig(output_path, dpi=300)
    plt.close()


In [18]:
def save_plp_plots_from_mp3s(input_dir, output_dir, n_ceps=13):
    """
    Process all MP3 files in a directory and save PLP plots as images.
    
    Parameters:
    -----------
    input_dir : str
        Directory containing MP3 files
    output_dir : str
        Directory to save plot images
    n_ceps : int
        Number of cepstral coefficients
    """
    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)
    
    # Get list of MP3 files
    mp3_files = [f for f in os.listdir(input_dir) if f.lower().endswith('.mp3')]
    
    if not mp3_files:
        print(f"No MP3 files found in {input_dir}")
        return
    
    # Process each MP3 file
    print(f"Processing {len(mp3_files)} MP3 files...")
    
    for mp3_file in tqdm(mp3_files):
        # Construct full input path
        input_path = os.path.join(input_dir, mp3_file)
        
        # Get base filename without extension
        base_name = os.path.splitext(mp3_file)[0]
        plot_path = os.path.join(output_dir, f"{base_name}_PLP.png")

        # Skip if plot already exists
        if os.path.exists(plot_path):
            print(f"Skipped {mp3_file}, plot already exists.")
            continue
        
        # Extract PLP coefficients and save plot
        try:
            # Extract PLP coefficients
            plp_features = extract_plp_from_mp3(input_path, n_ceps=n_ceps)
            
            # Save visualization
            plot_plp_coefficients(plp_features, plot_path)
            
            print(f"Saved plot for {mp3_file}")
            
        except Exception as e:
            print(f"Error processing {mp3_file}: {str(e)}")
    
    print(f"Processing complete. PLP plots saved to {output_dir}")

In [9]:
input_dir = "/data/sg2121/fypdataset/dataset_large/normal_data/human"
output_dir = "/data/sg2121/fypdataset/dataset_large/features/human/PLP"

save_plp_plots_from_mp3s(input_dir, output_dir)

Processing 7997 MP3 files...


  0%|                                                                               | 1/7997 [00:01<2:51:24,  1.29s/it]

Saved plot for H5951N.mp3


  0%|                                                                               | 2/7997 [00:02<2:57:29,  1.33s/it]

Saved plot for H7171N.mp3


...

Saved plot for H811N.mp3


100%|███████████████████████████████████████████████████████████████████████████▉| 7996/7997 [2:56:30<00:01,  1.31s/it]

Saved plot for H190N.mp3


100%|████████████████████████████████████████████████████████████████████████████| 7997/7997 [2:56:31<00:00,  1.32s/it]

Saved plot for H7568N.mp3
Processing complete. PLP plots saved to /data/sg2121/fypdataset/dataset_large/features/human/PLP


In [6]:
input_dir = "/data/sg2121/fypdataset/dataset_large/normal_data/ai_segments"
output_dir = "/data/sg2121/fypdataset/dataset_large/features/ai/PLP"

save_plp_plots_from_mp3s(input_dir, output_dir)

Processing 14147 MP3 files...


 23%|████████████████▉                                                         | 3228/14147 [00:00<00:00, 32271.57it/s]

Skipped S616RN_segment_2.mp3, plot already exists.
Skipped U548RN_segment_1.mp3, plot already exists.
Skipped S2934RN_segment_2.mp3, plot already exists.
Skipped S4839RN_segment_2.mp3, plot already exists.
Skipped S3016RN_segment_2.mp3, plot already exists.
Skipped S1209RN_segment_2.mp3, plot already exists.
Skipped S3907RN_segment_2.mp3, plot already exists.
Skipped S2872RN_segment_1.mp3, plot already exists.
Skipped S2118RN_segment_2.mp3, plot already exists.
Skipped U336R_segment_1.mp3, plot already exists.
Skipped S4783RN_segment_1.mp3, plot already exists.
Skipped S292RN_segment_1.mp3, plot already exists.
Skipped S3744RN_segment_1.mp3, plot already exists.
Skipped S329RN_segment_1.mp3, plot already exists.
Skipped S514RN_segment_2.mp3, plot already exists.
Skipped S4239RN_segment_1.mp3, plot already exists.
Skipped U1120RN_segment_1.mp3, plot already exists.
Skipped S3433RN_segment_1.mp3, plot already exists.
Skipped U577RN_segment_1.mp3, plot already exists.
Skipped U350RN_segme

 73%|█████████████████████████████████████████████████████▍                   | 10344/14147 [00:00<00:00, 34551.02it/s]

Skipped S3609RN_segment_1.mp3, plot already exists.
Skipped S2061RN_segment_2.mp3, plot already exists.
Skipped U1422RN_segment_1.mp3, plot already exists.
Skipped S2771RN_segment_2.mp3, plot already exists.
Skipped S654RN_segment_1.mp3, plot already exists.
Skipped S812RN_segment_2.mp3, plot already exists.
Skipped S1256RN_segment_2.mp3, plot already exists.
Skipped S1021RN_segment_1.mp3, plot already exists.
Skipped S4565RN_segment_1.mp3, plot already exists.
Skipped S1823RN_segment_2.mp3, plot already exists.
Skipped S4159RN_segment_1.mp3, plot already exists.
Skipped S2376RN_segment_2.mp3, plot already exists.
Skipped S3101RN_segment_1.mp3, plot already exists.
Skipped S2328RN_segment_2.mp3, plot already exists.
Skipped U1816RN_segment_1.mp3, plot already exists.
Skipped S1136RN_segment_2.mp3, plot already exists.
Skipped S2406RN_segment_1.mp3, plot already exists.
Skipped S253RN_segment_2.mp3, plot already exists.
Skipped S26RN_segment_2.mp3, plot already exists.
Skipped S3073RN_s

...

Saved plot for S4541RN_segment_1.mp3


100%|█████████████████████████████████████████████████████████████████████████▉| 14146/14147 [1:43:13<00:01,  1.95s/it]

Saved plot for S2131RN_segment_2.mp3


100%|██████████████████████████████████████████████████████████████████████████| 14147/14147 [1:43:15<00:00,  2.28it/s]

Saved plot for U183RN_segment_1.mp3
Processing complete. PLP plots saved to /data/sg2121/fypdataset/dataset_large/features/ai/PLP


In [ ]:
# https://medium.com/@imabhi1216/fine-tuning-a-pre-trained-resnet-18-model-for-image-classification-on-custom-dataset-with-pytorch-02df12e83c2c

In [1]:
import os
import shutil
from sklearn.model_selection import train_test_split
import random

import torch
import torchvision.models as models

from torchvision.datasets import ImageFolder
from torchvision.transforms import transforms
from torch.utils.data import Dataset, DataLoader

import time
from datetime import datetime
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, confusion_matrix

import pandas as pd
import torch.nn.functional as F

from PIL import Image

from tqdm import tqdm

from itertools import product

In [2]:
def get_model():
    # Load the pre-trained ResNet-18 model
    model = models.resnet34(weights=models.ResNet34_Weights.DEFAULT)

    # Modify the last layer of the model
    num_classes = 2 # number of classes in dataset
    model.fc = torch.nn.Linear(model.fc.in_features, num_classes)
    return model

In [3]:
# Directory paths for the segments and lyrics
ai_segments_path = "/data/sg2121/fypdataset/dataset_large/normal_data/ai_segments"
human_segments_path = "/data/sg2121/fypdataset/dataset_large/normal_data/human"
ai_plp_path = "/data/sg2121/fypdataset/dataset_large/features/ai/PLP"
human_plp_path = "/data/sg2121/fypdataset/dataset_large/features/human/PLP"

# Helper function to read file paths from a text file
def read_file_paths(file_name):
    with open(file_name, 'r') as f:
        return [line.strip() for line in f.readlines()]

# Read all file paths from the text files
train_files = read_file_paths('/data/sg2121/aimusicdetector/train_test_split/train_files_large.txt')
val_files = read_file_paths('/data/sg2121/aimusicdetector/train_test_split/val_files_large.txt')
test_files = read_file_paths('/data/sg2121/aimusicdetector/train_test_split/test_files_large.txt')


# Function to convert segment file path to lyric file path
def convert_to_plp_path(file_path, is_ai):
    if is_ai:
        if file_path.startswith(ai_segments_path):
            base_plp_path = ai_plp_path
        else:
            return
    else:
        if file_path.startswith(human_segments_path):
            base_plp_path = human_plp_path
        else:
            return

    # Convert filename to plp filename
    file_name = os.path.basename(file_path).replace('.mp3', '_PLP.png')
    return os.path.join(base_plp_path, file_name)


# Process the file lists and create tuples of (lyric_path, label)
def process_file_paths(file_paths, is_ai):
    return [(convert_to_plp_path(file_path, is_ai), 0 if is_ai else 1) for file_path in file_paths]

# Convert all file paths from the train, validation, and test sets
ai_train_files = process_file_paths(train_files, is_ai=True)
human_train_files = process_file_paths(train_files, is_ai=False)

ai_val_files = process_file_paths(val_files, is_ai=True)
human_val_files = process_file_paths(val_files, is_ai=False)

ai_test_files = process_file_paths(test_files, is_ai=True)
human_test_files = process_file_paths(test_files, is_ai=False)

def clean(paths):
    return [(p, l) for p, l in paths if p is not None]

def check(paths):
    return [(p, l) for (p, l) in paths if os.path.exists(p)]


train_files_combined = check(clean(ai_train_files) + clean(human_train_files))
val_files_combined = check(clean(ai_val_files) + clean(human_val_files))
test_files_combined = check(clean(ai_test_files) + clean(human_test_files))

# Shuffle the data if needed
random.shuffle(train_files_combined)
random.shuffle(val_files_combined)
random.shuffle(test_files_combined)

# Example of how you might check the splits
print(f"Training set size: {len(train_files_combined)}")
print(f"Validation set size: {len(val_files_combined)}")
print(f"Test set size: {len(test_files_combined)}")

Training set size: 15499
Validation set size: 3321
Test set size: 3324


In [4]:
# Custom dataset class
class PLPDataset(Dataset):
    def __init__(self, data, transform=None):
        self.data = data
        self.transform = transform

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        path, label = self.data[idx]
        filename = os.path.basename(path)

        try:
            image = Image.open(path).convert('RGB')
        except FileNotFoundError:
            print(f"{filename} not found.")
            raise IndexError(f"{filename} not found")  # Or raise a dummy image if you want to proceed

        if self.transform:
            image = self.transform(image)

        return image, label, filename
        
transform = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])


In [5]:
# Create datasets
train_dataset = PLPDataset(train_files_combined, transform=transform)
val_dataset = PLPDataset(val_files_combined, transform=transform)
test_dataset = PLPDataset(test_files_combined, transform=transform)

# DataLoaders
batch_size = 32
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)

# Confirm sizes
print(f"Train set: {len(train_dataset)} samples")
print(f"Val set: {len(val_dataset)} samples")
print(f"Test set: {len(test_dataset)} samples")

Train set: 15499 samples
Val set: 3321 samples
Test set: 3324 samples


In [6]:
# Determine whether to use GPU (if available) or CPU
device = torch.device("mps" if torch.backends.mps.is_available() else "cuda" if torch.cuda.is_available() else "cpu")
print(device)

def train(model, train_loader, val_loader, criterion, optimizer, num_epochs):
    
    for epoch in range(num_epochs):
        # Set the model to training mode
        model.train()

        # Initialize running loss and correct predictions count for training
        running_loss = 0.0
        running_corrects = 0

        # Iterate over the training data loader
        for inputs, labels, filenames in train_loader:
            # Move inputs and labels to the device (GPU or CPU)
            inputs = inputs.to(device)
            labels = labels.to(device)

            # Reset the gradients to zero before the backward pass
            optimizer.zero_grad()

            # Forward pass: compute the model output
            outputs = model(inputs)
            # Get the predicted class (with the highest score)
            _, preds = torch.max(outputs, 1)
            # Compute the loss between the predictions and actual labels
            loss = criterion(outputs, labels)

            # Backward pass: compute gradients
            loss.backward()
            # Perform the optimization step to update model parameters
            optimizer.step()

            # Accumulate the running loss and the number of correct predictions
            running_loss += loss.item() * inputs.size(0)
            running_corrects += torch.sum(preds == labels.data)

        # Compute average training loss and accuracy for this epoch
        train_loss = running_loss / len(train_loader.dataset)
        train_acc = running_corrects.float() / len(train_loader.dataset)

        # Set the model to evaluation mode for validation
        model.eval()
        # Initialize running loss and correct predictions count for validation
        running_loss = 0.0
        running_corrects = 0

        # Disable gradient computation for validation (saves memory and computations)
        with torch.no_grad():
            # Iterate over the validation data loader
            for inputs, labels, filenames in val_loader:
                # Move inputs and labels to the device (GPU or CPU)
                inputs = inputs.to(device)
                labels = labels.to(device)

                # Forward pass: compute the model output
                outputs = model(inputs)
                # Get the predicted class (with the highest score)
                _, preds = torch.max(outputs, 1)
                # Compute the loss between the predictions and actual labels
                loss = criterion(outputs, labels)

                # Accumulate the running loss and the number of correct predictions
                running_loss += loss.item() * inputs.size(0)
                running_corrects += torch.sum(preds == labels.data)

        # Compute average validation loss and accuracy for this epoch
        val_loss = running_loss / len(val_loader.dataset)
        val_acc = running_corrects.float() / len(val_loader.dataset)

        # Print the results for the current epoch
        print(f'Epoch [{epoch+1}/{num_epochs}], train loss: {train_loss:.4f}, train acc: {train_acc:.4f}, val loss: {val_loss:.4f}, val acc: {val_acc:.4f}')

cuda


In [9]:
model = get_model()
model = model.to(device)

# Define the loss function and optimizer
lr = 0.001
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.SGD(model.fc.parameters(), lr, momentum=0.9)
num_epochs = 5

train(model, train_loader, val_loader, criterion, optimizer, num_epochs)

Epoch [1/5], train loss: 0.5408, train acc: 0.7246, val loss: 0.4886, val acc: 0.7507
Epoch [2/5], train loss: 0.5062, train acc: 0.7504, val loss: 0.4845, val acc: 0.7687
Epoch [3/5], train loss: 0.4905, train acc: 0.7632, val loss: 0.4927, val acc: 0.7474


KeyboardInterrupt: 

In [10]:
def evaluate_model(model, test_loader, device, hyperparams=None):
    log_file = "/data/sg2121/aimusicdetector/music_cnn/large/plp/training_large_logfile.txt"

    model.eval()
    correct_pred = {classname: 0 for classname in ['ai', 'human']}
    total_pred = {classname: 0 for classname in ['ai', 'human']}

    all_labels = []
    all_preds = []
    
    start_time = time.time()

    with torch.no_grad():
        for inputs, labels, filenames in test_loader:
            inputs = inputs.to(device)
            labels = labels.to(device)

            outputs = model(inputs)
            probs = F.softmax(outputs, dim=1)
            _, preds = torch.max(outputs, 1)

            all_labels.extend(labels.cpu().numpy())
            all_preds.extend(preds.cpu().numpy())

            for label, prediction in zip(labels, preds):
                classname = 'ai' if label.item() == 0 else 'human'
                if label == prediction:
                    correct_pred[classname] += 1
                total_pred[classname] += 1

    end_time = time.time()
    avg_inference_time = (end_time - start_time) / len(test_loader.dataset)

    accuracy_per_class = {
        classname: correct_pred[classname] / total_pred[classname]
        if total_pred[classname] > 0 else 0
        for classname in ['ai', 'human']
    }

    overall_accuracy = accuracy_score(all_labels, all_preds)
    precision, recall, f1, _ = precision_recall_fscore_support(all_labels, all_preds, average=None, labels=[0, 1])
    cm = confusion_matrix(all_labels, all_preds)

    fpr = {}
    for i, classname in enumerate(['ai', 'human']):
        FP = cm[:, i].sum() - cm[i, i]
        TN = cm.sum() - (cm[i, :].sum() + cm[:, i].sum() - cm[i, i])
        fpr[classname] = FP / (FP + TN) if (FP + TN) > 0 else 0

    # Logging
    timestamp = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    log_lines = [f"===== Evaluation at {timestamp} =====\n"]

    if hyperparams:
        log_lines.append("Hyperparameters:")
        for key, value in hyperparams.items():
            log_lines.append(f"{key}: {value}")
    else:
        log_lines.append("No hyperparameters provided.")
    log_lines.append("")

    log_lines.append("Accuracy per class:")
    for classname, acc in accuracy_per_class.items():
        log_lines.append(f"{classname}: {acc:.4f}")
    log_lines.append("\nPrecision, Recall, F1:")
    for i, classname in enumerate(['ai', 'human']):
        log_lines.append(f"{classname} → Precision: {precision[i]:.4f}, Recall: {recall[i]:.4f}, F1: {f1[i]:.4f}")
    log_lines.append("\nFalse Positive Rate:")
    for classname, rate in fpr.items():
        log_lines.append(f"{classname}: {rate:.4f}")
    log_lines.append(f"\nOverall Accuracy: {overall_accuracy:.4f}")
    log_lines.append(f"Average Inference Time per Sample: {avg_inference_time:.6f} seconds")
    log_lines.append("=" * 40 + "\n\n")

    print("\n".join(log_lines))
    with open(log_file, "a") as f:
        f.write("\n".join(log_lines))

    return overall_accuracy


In [ ]:
model.eval()
results = []

for batch in tqdm(test_loader):
    inputs, labels, filenames = batch  # Unpack the filename from the dataset
    inputs = inputs.to(device)
    labels = labels.to(device)

    with torch.no_grad():
        outputs = model(inputs)
        probs = F.softmax(outputs, dim=1)

        for i in range(len(filenames)):
            results.append({
                "filename": filenames[i],  # Use filename directly from dataset
                "prob_ai": probs[i][0].item(),
                "prob_human": probs[i][1].item(),
                "true_label": labels[i].item(),
                "pred_label": torch.argmax(probs[i]).item()
            })

# Convert the results to a DataFrame
df = pd.DataFrame(results)

# Save to CSV
df.to_csv("plp_test_large_predictions.csv", index=False)

# Preview results
print(df.head())


In [ ]:
hyperparams = {
    "batch_size": batch_size,
    "learning_rate": lr,
    "epochs": num_epochs,
    "optimizer": optimizer,
    "model": model.__class__.__name__,
}

evaluate_model(model, test_loader, device, hyperparams=hyperparams)


In [11]:
# Define hyperparameter search space
learning_rates = [1e-3, 1e-4, 5e-4]
weight_decays = [1e-6, 1e-7, 1e-8]
epochs_list = [5, 10, 20] 

# Generate hyperparameter combinations and randomly select 10
param_combinations = list(product(learning_rates, weight_decays, epochs_list))
random.shuffle(param_combinations)
hyperparam_trials = param_combinations[:10]

# Run randomized search
best_model = None
best_acc = 0

for i, (lr, wd, epochs) in enumerate(hyperparam_trials):
    print(f"\n=== Trial {i+1}/10: LR={lr}, WD={wd}, Epochs={epochs} ===")

    model = get_model()
    model = model.to(device)
    
    # Use an optimizer like Adam or SGD (adjust based on your requirement)
    optimizer = torch.optim.SGD(model.parameters(), lr=lr, momentum=0.9, weight_decay=wd)
    
    # Train the model (assuming you have a function to handle training)
    train(model, train_loader, val_loader, criterion, optimizer, epochs)

    hyperparams = {
        "batch_size": batch_size,
        "learning_rate": lr,
        "epochs": epochs,
        "optimizer": optimizer,
        "model": model.__class__.__name__,
    }
    
    val_acc = evaluate_model(model, val_loader, device, hyperparams=hyperparams)
    if val_acc > best_acc:
        best_acc = val_acc
        best_model = model
        torch.save(model.state_dict(), 'best_model.pt')
    
print("\nBest validation accuracy:", best_acc)


=== Trial 1/10: LR=0.0001, WD=1e-08, Epochs=10 ===
Epoch [1/10], train loss: 0.5028, train acc: 0.7453, val loss: 0.4157, val acc: 0.8004
Epoch [2/10], train loss: 0.3842, train acc: 0.8239, val loss: 0.3754, val acc: 0.8299
Epoch [3/10], train loss: 0.3391, train acc: 0.8492, val loss: 0.3602, val acc: 0.8344
Epoch [4/10], train loss: 0.3021, train acc: 0.8678, val loss: 0.3448, val acc: 0.8416
Epoch [5/10], train loss: 0.2621, train acc: 0.8891, val loss: 0.3620, val acc: 0.8425
Epoch [6/10], train loss: 0.2333, train acc: 0.9015, val loss: 0.3576, val acc: 0.8416
Epoch [7/10], train loss: 0.1956, train acc: 0.9220, val loss: 0.3600, val acc: 0.8470
Epoch [8/10], train loss: 0.1630, train acc: 0.9381, val loss: 0.3674, val acc: 0.8422
Epoch [9/10], train loss: 0.1328, train acc: 0.9506, val loss: 0.4027, val acc: 0.8335
Epoch [10/10], train loss: 0.1041, train acc: 0.9655, val loss: 0.4312, val acc: 0.8353
===== Evaluation at 2025-05-12 23:16:39 =====

Hyperparameters:
batch_size: 3

In [12]:
model = get_model()
model.load_state_dict(torch.load("best_model.pt", map_location=device))
model.to(device)
model.eval()
results = []

for batch in tqdm(test_loader):
    inputs, labels, filenames = batch  # Unpack the filename from the dataset
    inputs = inputs.to(device)
    labels = labels.to(device)

    with torch.no_grad():
        outputs = model(inputs)
        probs = F.softmax(outputs, dim=1)

        for i in range(len(filenames)):
            results.append({
                "filename": filenames[i],  # Use filename directly from dataset
                "prob_ai": probs[i][0].item(),
                "prob_human": probs[i][1].item(),
                "true_label": labels[i].item(),
                "pred_label": torch.argmax(probs[i]).item()
            })

# Convert the results to a DataFrame
df = pd.DataFrame(results)

# Save to CSV
df.to_csv("best_plp_test_large_predictions.csv", index=False)

# Preview results
print(df.head())


100%|█████████████████████████████████████████████████████████████| 104/104 [05:39<00:00,  3.27s/it]


                    filename   prob_ai    prob_human  true_label  pred_label
0  S4256RN_segment_2_PLP.png  1.000000  1.539712e-10           0           0
1  S2979RN_segment_1_PLP.png  1.000000  5.211529e-11           0           0
2             H4269N_PLP.png  0.999982  1.851184e-05           1           0
3   S706RN_segment_2_PLP.png  1.000000  3.712870e-16           0           0
4  U1840RN_segment_2_PLP.png  1.000000  3.693166e-08           0           0
